<h1 align=center><font size = 5>Capstone Project - The Battle of the Neighborhoods</font></h1>

## Applied Data Science Capstone by IBM/Coursera

## Table of Contents

<div class="alert alert-block alert-info" style="margin-top: 20px">

1. [Introduction: Business Problem](#0)<br>
2. [Data](#2)<br>
3. [Methodology](#4) <br>
4. [Results and Discussion ](#6) <br>
5. [Conclusion](#8) <br>
</div>
<hr>

## Introduction: Business Problem

The goal of this project is to help anybody who doesn't know Paris and would like to buy a house or an apartment with somehow the best possible value for money. Indeed, in Paris, like any big city, you have many very different neighborhoods, each of them has its advantages and disadvantages so it is hard to find the best place to live especially if you don't know already the city.

In this project will we consider that a good place to live is a place located near at least one subway station and as many venues as possible because we want a living place with a lot of activities around it and all this for the lowest price as possible.


## Data

To fulfill the requirements of this project, we will need several data sources:
* https://opendata.paris.fr to get the shape of Paris and its boroughs, it will be used to filter and better locate the potential locations.
* http://dataratp.download.opendatasoft.com to retrieve the positions of all existing subway stations, it will be used to keep only the locations close to one of them.
* https://cadastre.data.gouv.fr to have all the transactions of houses or apartments in Paris since 2014, it will be used to get the average price by square meter.
* https://api.foursquare.com to get all the venues close to each potential location.
* https://nominatim.openstreetmap.org to retrieve the addresses corresponding to our final potential locations.



## Methodology

The first thing to do is to import everything that will be needed in this notebook.

In [2]:
import numpy as np
import pandas as pd
import requests
!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim
!conda install -c conda-forge folium=0.10.0 --yes
from geopy.distance import geodesic
import math
import folium
!conda install -c conda-forge shapely --yes 
from shapely.geometry import Point
from shapely.geometry.polygon import Polygon
from folium import plugins
from folium.plugins import HeatMap
import requests
import zipfile
from sklearn.cluster import KMeans
from sklearn.preprocessing import StandardScaler

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    certifi-2019.9.11          |           py36_0         147 KB  conda-forge
    openssl-1.1.1c             |       h516909a_0         2.1 MB  conda-forge
    geopy-1.20.0               |             py_0          57 KB  conda-forge
    ca-certificates-2019.9.11  |       hecc5488_0         144 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.5 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.50-py_0         conda-forge
    geopy:           1.20.0-py_0       conda-forge

The following packages will be UPDATED:

    ca-

---

Throughout this notebook, we will consider that something is close to a given location if it is located within 200 meters. 

So let's first fix the value of the variable *maxRadius* representing this distance.

In [3]:
maxRadius = 200

Now, let's retrieve the geographic coordinates of Paris thanks to **geopy**

In [4]:
geolocator = Nominatim(user_agent='capstone')
location = geolocator.geocode("Paris")
paris_center = [location.latitude, location.longitude]
print("latitude=", paris_center[0], "longitude=",paris_center[1])

latitude= 48.8566101 longitude= 2.3514992


Let's now retrieve the shape of Paris and its boroughs

In [5]:
paris_boroughs_url = 'https://opendata.paris.fr/explore/dataset/arrondissements/download/?format=geojson&timezone=Europe/Berlin'
paris_boroughs = requests.get(paris_boroughs_url).json()

def boroughs_style(feature):
    return { 'color': 'black', 'fill': True, 'fill_opacity': 0.4}

We can now display the map of Paris and its boroughs

In [7]:
map_paris = folium.Map(location=paris_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_paris) #cartodbpositron cartodbdark_matter
for feature in paris_boroughs["features"]:
    folium.Marker(
        location=feature["properties"]["geom_x_y"],
        popup=feature["properties"]["l_ar"],
        icon=folium.Icon(color='green')
    ).add_to(map_paris)
folium.GeoJson(paris_boroughs, style_function=boroughs_style, name='geojson').add_to(map_paris)
map_paris

Now, we need to identify all the potential locations to study. 

For that: 
1. We need to define the rectangle that contains entirely Paris by getting the minimum and maximum latitude and longitude
1. We then find the middle of that rectangle
1. From that middle, we compute the distance between the middle and the top-right edge of the rectangle, this distance is the radius of the circle that will contain the rectangle.
1. We then check if this distance is equal to or below 200 meters if so we keep this middle as a potential location, otherwise, we split the  rectangle into 4 rectangles (top left, top right, bottom right, and bottom left) and we go back to step #2

If we strictly apply the algorithm described previously, we will get **4096** potential locations that actually cover the entire rectangle which contains Paris but as Paris is not a rectangle, most of them are outside the city, so at step #4 we add an extra filter to keep only the locations that are inside the city. Thanks to this filter, we end up with **2487** potential locations in the **20** boroughs of Paris.

In [8]:
minLatitude = float('inf')
maxLatitude = float('-inf')
minLongitude = float('inf')
maxLongitude = float('-inf')

for feature in paris_boroughs["features"]:
    for coordinates in feature["geometry"]["coordinates"][0]:
        if (coordinates[1] < minLatitude):
            minLatitude = coordinates[1]
        if (coordinates[1] > maxLatitude):
            maxLatitude = coordinates[1]
        if (coordinates[0] < minLongitude):
            minLongitude = coordinates[0]
        if (coordinates[0] > maxLongitude):
            maxLongitude = coordinates[0]
centerLatitude = (maxLatitude + minLatitude) / 2
centerLongitude = (maxLongitude + minLongitude) / 2

polygons = []
for feature in paris_boroughs["features"]:
    polygons.append(Polygon(feature["geometry"]["coordinates"][0]))
print("Found", len(polygons), "boroughs in paris")
    
def is_in_paris(centerLatitude, centerLongitude):
    point = Point(centerLongitude, centerLatitude)
    for polygon in polygons:
        if (polygon.contains(point)):
            return True
    return False


def add_centers(centers, centerLatitude, centerLongitude, minLatitude, maxLatitude, minLongitude, maxLongitude, maxRadius):
    height = geodesic((minLatitude, centerLongitude), (maxLatitude, centerLongitude)).meters
    width = geodesic((centerLatitude, minLongitude), (centerLatitude, maxLongitude)).meters
    radius = math.sqrt((height/2)**2 + (width/2)**2)
    if radius <= maxRadius :
        if is_in_paris(centerLatitude, centerLongitude):
            centers.append([centerLatitude, centerLongitude])
    else :
        # slip in 4 centers
        # Upper right
        add_centers(centers, (centerLatitude + maxLatitude) / 2, (centerLongitude + maxLongitude) / 2, centerLatitude, maxLatitude, centerLongitude, maxLongitude, maxRadius)
        # Upper left
        add_centers(centers, (centerLatitude + maxLatitude) / 2, (centerLongitude + minLongitude) / 2, centerLatitude, maxLatitude, minLongitude, centerLongitude, maxRadius)
        # Lower right
        add_centers(centers, (centerLatitude + minLatitude) / 2, (centerLongitude + maxLongitude) / 2, minLatitude, centerLatitude, centerLongitude, maxLongitude, maxRadius)
        # Lower left
        add_centers(centers, (centerLatitude + minLatitude) / 2, (centerLongitude + minLongitude) / 2, minLatitude, centerLatitude, minLongitude, centerLongitude, maxRadius)

centers = []
add_centers(centers, centerLatitude, centerLongitude, minLatitude, maxLatitude, minLongitude, maxLongitude, maxRadius)
df_centers = pd.DataFrame(centers, columns = ['latitude', 'longitude'])
print("Found",df_centers.shape[0],"centers")

Found 20 boroughs in paris
Found 2487 centers


Let's have a look at our potential locations on the map of Paris

In [9]:
map_paris = folium.Map(location=paris_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_paris) #cartodbpositron cartodbdark_matter
for feature in paris_boroughs["features"]:
    folium.Marker(
        location=feature["properties"]["geom_x_y"],
        popup=feature["properties"]["l_ar"],
        icon=folium.Icon(color='green')
    ).add_to(map_paris)
folium.GeoJson(paris_boroughs, style_function=boroughs_style, name='geojson').add_to(map_paris)
for center in df_centers.values.tolist():
    folium.Circle(center, radius=maxRadius, color='blue', fill=True, fill_opacity=0.1).add_to(map_paris)
map_paris

As you can see on the map above, Paris is fully covered by the potential locations but we still need to reduce them by keeping only those which have at least one subway station nearby. 

So now, we need to retrieve all the subway stations.

In [10]:
!wget -q -O 'RATP_GTFS_LINES.zip' http://dataratp.download.opendatasoft.com/RATP_GTFS_LINES.zip
paris_subway_station_df = pd.DataFrame()
with zipfile.ZipFile('RATP_GTFS_LINES.zip') as zip:
    for zipfileName in zip.namelist():
        if zipfileName.startswith("RATP_GTFS_METRO_") and zipfileName.endswith('.zip') and zipfileName != 'RATP_GTFS_METRO_Fun.zip' and zipfileName != 'RATP_GTFS_METRO_Orv.zip':
            zip.extract(zipfileName)
            with zipfile.ZipFile(zipfileName) as innerZip:
                with innerZip.open('stops.txt') as myZip:
                    paris_subway_station_df = paris_subway_station_df.append(pd.read_csv(myZip), sort=False)
print("Data Downloaded")

Data Downloaded


Once we have loaded the data, we need to clean it to keep only what we need.

So we:
1. Keep only the columns that we need which are the name, the latitude, and longitude
1. Rename the columns to have more explicit names
1. Remove all the duplicates to keep only the first occurrence
1. Sort them by name (this step is not mandatory but it makes the list easier to read)

In [11]:
paris_subway_station_df = paris_subway_station_df[['stop_name', 'stop_lat', 'stop_lon']]
paris_subway_station_df.rename(columns={'stop_name': 'name', 'stop_lat': 'latitude', 'stop_lon': 'longitude'}, inplace=True)
paris_subway_station_df.drop_duplicates(subset='name', keep = 'first', inplace = True)
paris_subway_station_df.sort_values('name', inplace = True)
paris_subway_station_df

name   latitude  longitude
18                                           Abbesses  48.884400   2.338399
19                                    Alexandre-Dumas  48.856408   2.394500
7                                        Alma-Marceau  48.864299   2.301251
25                                             Alésia  48.828066   2.326827
7                                      Anatole-France  48.892019   2.285517
16                                             Anvers  48.882872   2.344164
10                                          Argentine  48.875672   2.289444
13                                    Arts-et-Métiers  48.865381   2.355645
42              Asnières-Gennevilliers Les Courtilles  48.930294   2.283761
11                                Assemblée Nationale  48.861454   2.320310
20                   Aubervilliers Pantin (4 Chemins)  48.903898   2.392480
29                                  Avenue Emile-Zola  48.846852   2.295449
20                                              Avron  48.851194   2.398239
54                                             Balard  48.836815   2.278683
9                                 Barbès-Rochechouart  48.883680   2.349533
34                           Basilique de Saint-Denis  48.936477   2.359640
3                                            Bastille  48.852976   2.369219
5                                             Bel-Air  48.841432   2.400869
2                                          Belleville  48.871946   2.376751
3                                               Bercy  48.840543   2.379409
11                   Bibliothèque-François Mitterrand  48.829831   2.376120
0                                         Billancourt  48.832088   2.238161
8                               Bir-Hakeim (Grenelle)  48.854327   2.288810
13                                            Blanche  48.883771   2.332485
2                               Bobigny-Pablo-Picasso  48.907147   2.449458
12                   Bobigny-Pantin (Raymond Queneau)  48.895799   2.424857
46                                          Boissière  48.866856   2.290038
1                                             Bolivar  48.880790   2.374155
30                                     Bonne Nouvelle  48.870577   2.348494
4                                            Botzaris  48.879607   2.389416
..                                                ...        ...        ...
5                                       Saint-Sulpice  48.851146   2.330963
19                          Saint-Sébastien-Froissart  48.860975   2.367262
1                                             Sentier  48.867350   2.347567
0                                             Simplon  48.894043   2.347314
1                                           Solférino  48.858533   2.323089
15                                         Stalingrad  48.884189   2.367030
10                             Strasbourg-Saint-Denis  48.869632   2.354502
41                                      Sully-Morland  48.850794   2.361237
2                                     Sèvres-Babylone  48.850939   2.326115
2                                     Sèvres-Lecourbe  48.844996   2.310865
0                                               Ségur  48.846865   2.307269
31                                             Temple  48.866764   2.361571
30                                             Ternes  48.878228   2.298121
33                                            Tolbiac  48.826159   2.357019
26                         Trinité-d'Estienne d'Orves  48.876329   2.331805
25                                          Trocadéro  48.862667   2.287263
22                                          Tuileries  48.864780   2.329095
3                                          Télégraphe  48.875522   2.398677
4                                              Vaneau  48.848701   2.321240
17                                            Varenne  48.856393   2.314754
5                        Vaugirard (Adolphe Chérioux)  48.839439   2.301078
2                    

Let's display them on the map of Paris

In [12]:
map_paris = folium.Map(location=paris_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_paris) #cartodbpositron cartodbdark_matter
folium.GeoJson(paris_boroughs, style_function=boroughs_style, name='geojson').add_to(map_paris)
for index, row in paris_subway_station_df.iterrows():
    folium.CircleMarker([row["latitude"], row["longitude"]], popup=row["name"].replace("'", "&#39;"), radius=3, color='grey', fill=True, fill_color='blue', fill_opacity=1).add_to(map_paris)
map_paris

In [13]:
def is_in_circle(centerLatitude, centerLongitude, latitude, longitude, maxDistance):
    return True if geodesic((centerLatitude, centerLongitude), (latitude, longitude)).meters <= maxDistance else False

From here, we will simply iterator over all the potential locations and count how many subway stations we have nearby.

In [14]:
subwayStations = []
for i, rowCenters in df_centers.iterrows():
    total = 0
    centerLatitude = rowCenters["latitude"]
    centerLongitude = rowCenters["longitude"]
    for j, rowStations in paris_subway_station_df.iterrows():
        if is_in_circle(centerLatitude, centerLongitude, rowStations["latitude"], rowStations["longitude"], maxRadius):
            total = total + 1
    subwayStations.append(total)
    print(' {}'.format(total), end='')
print(' done.')    
df_centers["stations"] = subwayStations
df_centers.to_csv("df_centers.csv")
df_centers

 0 0 0 0 0 0 0 0 0 1 0 1 0 0 1 0 0 0 0 0 0 1 0 0 1 0 1 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 1 0 0 1 0 1 0 0 0 1 0 1 0 0 0 0 1 0 0 0 0 0 1 1 0 1 0 0 0 1 0 0 0 0 0 0 1 1 1 0 1 0 0 0 1 0 1 1 0 1 0 0 0 0 0 1 0 2 0 0 0 0 0 1 1 0 0 0 0 0 0 1 0 1 0 0 1 0 0 0 0 0 0 0 1 0 1 0 0 0 1 1 0 2 0 0 1 1 1 2 1 0 1 1 0 1 0 0 1 0 1 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 1 1 0 0 0 0 0 0 0 1 0 1 0 1 0 1 0 1 0 1 1 1 1 1 1 1 0 0 0 1 1 1 0 2 1 1 1 0 0 0 0 0 1 1 0 0 0 1 1 0 1 0 0 0 0 1 2 0 1 1 0 1 0 0 0 0 0 0 0 0 1 1 1 0 1 0 1 1 1 0 1 0 0 1 0 0 0 1 1 1 1 1 0 1 1 2 1 0 1 0 1 0 1 0 0 1 0 0 0 0 0 1 0 1 1 0 0 0 0 0 0 0 1 0 0 0 0 1 1 1 1 0 1 1 1 0 1 0 1 0 0 1 0 0 0 1 0 1 0 1 0 0 0 0 0 0 1 0 1 0 0 0 1 1 0 1 1 1 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 1 0 1 1 1 0 0 0 0 1 0 0 0 0 0 0 1 0 0 0 0 0 1 1 0 1 0 1 2 1 0 1 1 1 0 1 1 1 1 1 1 0 1 1 1 1 1 1 0 1 2 2 1 2 0 0 2 0 1 1 0 1 0 0 0 0 0 0 1 1 2 0 0 0 0 1 0 1 1 0 0 0 0 1 0 1 0 0 0 0 0 0 0

latitude  longitude  stations
0     48.897427   2.394905         0
1     48.901485   2.387227         0
2     48.900133   2.391066         0
3     48.900133   2.387227         0
4     48.901485   2.383388         0
5     48.901485   2.379549         0
6     48.900133   2.383388         0
7     48.900133   2.379549         0
8     48.898780   2.391066         0
9     48.898780   2.387227         1
10    48.897427   2.391066         0
11    48.897427   2.387227         1
12    48.898780   2.383388         0
13    48.898780   2.379549         0
14    48.897427   2.383388         1
15    48.897427   2.379549         0
16    48.896074   2.394905         0
17    48.894721   2.394905         0
18    48.893368   2.394905         0
19    48.892015   2.394905         0
20    48.896074   2.391066         0
21    48.896074   2.387227         1
22    48.894721   2.391066         0
23    48.894721   2.387227         0
24    48.896074   2.383388         1
25    48.896074   2.379549         0
26    48.894721   2.383388         1
27    48.894721   2.379549         0
28    48.893368   2.391066         0
29    48.893368   2.387227         0
...         ...        ...       ...
2457  48.835194   2.283580         0
2458  48.835194   2.279741         1
2459  48.836547   2.275902         0
2460  48.836547   2.272063         0
2461  48.835194   2.275902         0
2462  48.835194   2.272063         0
2463  48.833841   2.283580         0
2464  48.833841   2.279741         0
2465  48.832488   2.283580         0
2466  48.832488   2.279741         0
2467  48.833841   2.275902         0
2468  48.833841   2.272063         0
2469  48.832488   2.275902         0
2470  48.832488   2.272063         0
2471  48.836547   2.268225         0
2472  48.836547   2.264386         0
2473  48.835194   2.268225         0
2474  48.835194   2.264386         0
2475  48.836547   2.260547         0
2476  48.836547   2.256708         1
2477  48.835194   2.260547         0
2478  48.835194   2.256708         0
2479  48.831135   2.283580         0
2480  48.831135   2.275902         0
2481  48.831135   2.272063         0
2482  48.829782   2.272063         0
2483  48.828429   2.272063         0
2484  48.831135   2.268225         0
2485  48.829782   2.268225         0
2486  48.828429   2.268225         0

[2487 rows x 3 columns]

In [15]:
df_centers = pd.read_csv("df_centers.csv")
df_centers = df_centers[["latitude", "longitude", "stations"]]
df_centers

latitude  longitude  stations
0     48.897427   2.394905         0
1     48.901485   2.387227         0
2     48.900133   2.391066         0
3     48.900133   2.387227         0
4     48.901485   2.383388         0
5     48.901485   2.379549         0
6     48.900133   2.383388         0
7     48.900133   2.379549         0
8     48.898780   2.391066         0
9     48.898780   2.387227         1
10    48.897427   2.391066         0
11    48.897427   2.387227         1
12    48.898780   2.383388         0
13    48.898780   2.379549         0
14    48.897427   2.383388         1
15    48.897427   2.379549         0
16    48.896074   2.394905         0
17    48.894721   2.394905         0
18    48.893368   2.394905         0
19    48.892015   2.394905         0
20    48.896074   2.391066         0
21    48.896074   2.387227         1
22    48.894721   2.391066         0
23    48.894721   2.387227         0
24    48.896074   2.383388         1
25    48.896074   2.379549         0
26    48.894721   2.383388         1
27    48.894721   2.379549         0
28    48.893368   2.391066         0
29    48.893368   2.387227         0
...         ...        ...       ...
2457  48.835194   2.283580         0
2458  48.835194   2.279741         1
2459  48.836547   2.275902         0
2460  48.836547   2.272063         0
2461  48.835194   2.275902         0
2462  48.835194   2.272063         0
2463  48.833841   2.283580         0
2464  48.833841   2.279741         0
2465  48.832488   2.283580         0
2466  48.832488   2.279741         0
2467  48.833841   2.275902         0
2468  48.833841   2.272063         0
2469  48.832488   2.275902         0
2470  48.832488   2.272063         0
2471  48.836547   2.268225         0
2472  48.836547   2.264386         0
2473  48.835194   2.268225         0
2474  48.835194   2.264386         0
2475  48.836547   2.260547         0
2476  48.836547   2.256708         1
2477  48.835194   2.260547         0
2478  48.835194   2.256708         0
2479  48.831135   2.283580         0
2480  48.831135   2.275902         0
2481  48.831135   2.272063         0
2482  48.829782   2.272063         0
2483  48.828429   2.272063         0
2484  48.831135   2.268225         0
2485  48.829782   2.268225         0
2486  48.828429   2.268225         0

[2487 rows x 3 columns]

We can now, keep only the potential locations that have at least one subway station nearby, which allows us to keep only **681** potential locations.

In [16]:
df_centers = df_centers[df_centers["stations"] > 0]
df_centers

latitude  longitude  stations
9     48.898780   2.387227         1
11    48.897427   2.387227         1
14    48.897427   2.383388         1
21    48.896074   2.387227         1
24    48.896074   2.383388         1
26    48.894721   2.383388         1
32    48.893368   2.383388         1
59    48.898780   2.360355         1
61    48.897427   2.360355         1
90    48.894721   2.348839         1
93    48.892015   2.360355         1
96    48.893368   2.348839         1
98    48.892015   2.348839         1
102   48.889309   2.394905         1
104   48.887957   2.394905         1
109   48.889309   2.391066         1
115   48.887957   2.391066         1
116   48.887957   2.387227         1
118   48.886604   2.387227         1
122   48.886604   2.379549         1
129   48.882545   2.394905         1
130   48.881192   2.398743         1
131   48.881192   2.394905         1
133   48.885251   2.387227         1
137   48.885251   2.379549         1
139   48.883898   2.379549         1
140   48.882545   2.391066         1
142   48.881192   2.391066         1
148   48.890662   2.375711         1
150   48.889309   2.375711         2
...         ...        ...       ...
2285  48.833841   2.337323         1
2286  48.833841   2.333484         1
2287  48.832488   2.337323         1
2296  48.835194   2.318129         1
2297  48.833841   2.329645         2
2299  48.832488   2.329645         1
2302  48.833841   2.318129         1
2304  48.832488   2.318129         1
2305  48.831135   2.345000         1
2306  48.831135   2.341162         1
2321  48.831135   2.329645         1
2330  48.828429   2.325806         1
2332  48.827076   2.325806         1
2347  48.832488   2.314290         1
2353  48.836547   2.298935         1
2354  48.836547   2.295096         1
2366  48.833841   2.287418         1
2368  48.832488   2.287418         1
2369  48.831135   2.314290         1
2381  48.828429   2.306612         1
2382  48.828429   2.302774         1
2383  48.827076   2.306612         1
2384  48.827076   2.302774         1
2390  48.831135   2.287418         1
2417  48.824370   2.325806         1
2423  48.823018   2.325806         1
2425  48.821665   2.325806         1
2456  48.836547   2.279741         1
2458  48.835194   2.279741         1
2476  48.836547   2.256708         1

[681 rows x 3 columns]

Let's display them with the subway stations on a map

In [17]:
map_paris = folium.Map(location=paris_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_paris) #cartodbpositron cartodbdark_matter
folium.GeoJson(paris_boroughs, style_function=boroughs_style, name='geojson').add_to(map_paris)
for i, row in paris_subway_station_df.iterrows():
    folium.CircleMarker([row["latitude"], row["longitude"]], popup=row["name"].replace("'", "&#39;"), radius=3, color='grey', fill=True, fill_color='blue', fill_opacity=1).add_to(map_paris)
for center in df_centers.values.tolist():
    folium.Circle(center[0:2], radius=maxRadius, color='blue', fill=True, fill_opacity=0.1).add_to(map_paris)
map_paris

At this stage, we can still have some potential locations that don't make sense as they could be located far from the houses.

To fix this issue, we will load all the transactions in Paris for the past 5 years. We assume that if no transactions have occurred near a potential location, it would mean that there is no house to buy/sell, so it could not be a candidate.

In [18]:
years = [2014, 2015, 2016, 2017, 2018]
paris_housing_sales_prices_df = pd.DataFrame()
for year in years:
    get_ipython().system("wget -q -O '{}-75.csv.gz' https://cadastre.data.gouv.fr/data/etalab-dvf/latest/csv/{}/departements/75.csv.gz".format(year, year))
    paris_housing_sales_prices_df = paris_housing_sales_prices_df.append(pd.read_csv('{}-75.csv.gz'.format(year)), sort=False)
print("Data Downloaded")

/opt/conda/envs/Python36/lib/python3.6/site-packages/IPython/core/interactiveshell.py:3020: DtypeWarning: Columns (18,20,22,35,36) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)
/opt/conda/envs/Python36/lib/python3.6/site-packages/IPython/core/interactiveshell.py:3020: DtypeWarning: Columns (18,20) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)
/opt/conda/envs/Python36/lib/python3.6/site-packages/IPython/core/interactiveshell.py:3020: DtypeWarning: Columns (17,18,20,22,24) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)
/opt/conda/envs/Python36/lib/python3.6/site-packages/IPython/core/interactiveshell.py:3020: DtypeWarning: Columns (8,18,20,35,36) have mixed types. Specify dtype option on import or set low_memory=Fa

Data Downloaded


Once we have loaded the data, we need to clean it to keep only what we need.

So we:

1. Keep only the transactions corresponding to house sales.
1. Keep only the transactions of houses or apartments.
1. Keep only the columns corresponding to the price, the total amount of square meters, latitude, and longitude.
1. Remove all the incomplete rows
1. Keep only the transactions with a price and total amount of square meters between 1 % and 99 % to get rid of suspicious/incorrect/invalid transactions
1. Compute the price by square meter
1. Compute the average price by square meter for a given latitude and longitude 
1. Keep only the transactions with an average price by square meters between 1 % and 99 % to get rid of suspicious/incorrect/invalid transactions

In [19]:
paris_housing_sales_prices_df = paris_housing_sales_prices_df[paris_housing_sales_prices_df['nature_mutation'] == 'Vente']
paris_housing_sales_prices_df = paris_housing_sales_prices_df[(paris_housing_sales_prices_df['type_local'] == 'Appartement') | (paris_housing_sales_prices_df['type_local'] == 'Maison')]
paris_housing_sales_prices_df = paris_housing_sales_prices_df[['valeur_fonciere', 'surface_reelle_bati', 'longitude', 'latitude']]
paris_housing_sales_prices_df = paris_housing_sales_prices_df.dropna()
paris_housing_sales_prices_df.columns = ['price', 'area', 'longitude', 'latitude']
firstOnePercentile = paris_housing_sales_prices_df.quantile(0.01)
lastOnePercentile = paris_housing_sales_prices_df.quantile(0.99)
paris_housing_sales_prices_df = paris_housing_sales_prices_df[paris_housing_sales_prices_df.area.gt(firstOnePercentile.area) & paris_housing_sales_prices_df.area.lt(lastOnePercentile.area)]
paris_housing_sales_prices_df = paris_housing_sales_prices_df[paris_housing_sales_prices_df.price.gt(firstOnePercentile.price) & paris_housing_sales_prices_df.price.lt(lastOnePercentile.price)]
paris_housing_sales_prices_df['price_by_square_meters'] = paris_housing_sales_prices_df['price'] / paris_housing_sales_prices_df['area']
paris_housing_sales_prices_df = paris_housing_sales_prices_df[['latitude', 'longitude', 'price_by_square_meters']].groupby(['latitude', 'longitude']).mean().reset_index()
paris_housing_sales_prices_df['price_by_square_meters'] = paris_housing_sales_prices_df['price_by_square_meters'].round(decimals=0)
firstOnePercentile = paris_housing_sales_prices_df.quantile(0.01)
lastOnePercentile = paris_housing_sales_prices_df.quantile(0.99)
paris_housing_sales_prices_df = paris_housing_sales_prices_df[paris_housing_sales_prices_df.price_by_square_meters.gt(firstOnePercentile.price_by_square_meters) & paris_housing_sales_prices_df.price_by_square_meters.lt(lastOnePercentile.price_by_square_meters)]
paris_housing_sales_prices_df

latitude  longitude  price_by_square_meters
0      48.819411   2.361019                  6890.0
1      48.819493   2.361323                  5976.0
2      48.819549   2.359776                  6307.0
3      48.819710   2.360005                  8533.0
4      48.819772   2.345436                  5674.0
5      48.819796   2.343914                  7394.0
6      48.820013   2.341797                  7594.0
7      48.820044   2.342016                  9535.0
8      48.820068   2.345805                  6471.0
9      48.820082   2.345656                  7649.0
10     48.820088   2.361732                  5522.0
11     48.820170   2.343230                  7385.0
12     48.820171   2.342349                  7407.0
13     48.820278   2.341788                  9336.0
14     48.820325   2.341920                  9044.0
15     48.820338   2.341718                  8730.0
16     48.820374   2.341667                  8316.0
17     48.820400   2.362636                  6612.0
18     48.820525   2.360998                  5798.0
19     48.820595   2.341620                  9765.0
20     48.820719   2.343022                 12246.0
21     48.820738   2.341916                  7870.0
22     48.820813   2.341677                  8115.0
23     48.820829   2.361522                  6944.0
24     48.820844   2.342899                  9119.0
25     48.820911   2.356071                  6704.0
26     48.820916   2.341521                 11540.0
27     48.821098   2.356149                  7152.0
28     48.821172   2.359762                  6868.0
29     48.821227   2.361203                  3750.0
...          ...        ...                     ...
36474  48.897478   2.346701                  8191.0
36475  48.897490   2.341657                 10039.0
36476  48.897503   2.341919                  6092.0
36477  48.897515   2.338132                119404.0
36478  48.897519   2.358599                  3832.0
36479  48.897521   2.334926                 46222.0
36480  48.897546   2.346776                  8176.0
36481  48.897558   2.336487                 14186.0
36482  48.897561   2.384883                  5585.0
36483  48.897577   2.338163                  6703.0
36484  48.897595   2.341395                  6198.0
36485  48.897608   2.347403                  6321.0
36486  48.897619   2.342837                  5935.0
36487  48.897621   2.358583                  7857.0
36488  48.897630   2.341765                 15992.0
36489  48.897635   2.360047                  4191.0
36490  48.897644   2.343103                  6451.0
36491  48.897647   2.342247                  8556.0
36492  48.897679   2.346854                  4661.0
36493  48.897683   2.343459                  7787.0
36494  48.897696   2.318601                  7818.0
36495  48.897699   2.347322                  8175.0
36497  48.897725   2.358636                  4940.0
36498  48.898055   2.384753                  4774.0
36499  48.898106   2.385468                  4357.0
36500  48.899180   2.377651                  8275.0
36501  48.899196   2.378428                  7269.0
36502  48.899795   2.321945                 60995.0
36503  48.900565   2.352550                  5451.0
36504  48.900722   2.344876                 61370.0

[35773 rows x 3 columns]

Let's now represent all those transactions thanks to a **HeatMap** to have an idea of the repartition.

In [20]:
map_paris = folium.Map(location=paris_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_paris) #cartodbpositron cartodbdark_matter
folium.GeoJson(paris_boroughs, style_function=boroughs_style, name='geojson').add_to(map_paris)
HeatMap(data=paris_housing_sales_prices_df.values.tolist(), radius=8, max_zoom=13).add_to(map_paris)
map_paris

As you can see above, there are several holes where we have no transaction, if we zoom in, we can realize that they correspond to parks, rivers and other things that prevent having houses there.

We want to get rid of all the potential locations that would not have transaction and for this, we will iterate over the potential locations to count how many transactions occurred nearby and compute the average price by square meters in the area.

As we have a lot of transactions, to optimize the overall process, we will first sort the potential locations and transaction by longitude and latitude to be able to reduce the total amount of transactions to check for each potential location.

In [21]:
df_centers = df_centers.sort_values(by=['longitude', 'latitude']).reset_index()
df_centers

index   latitude  longitude  stations
0     2476  48.836547   2.256708         1
1     2262  48.837899   2.256708         1
2     2220  48.847370   2.256708         1
3     2145  48.848723   2.256708         1
4     2251  48.841958   2.260547         1
5     2229  48.843311   2.260547         1
6     2227  48.844664   2.260547         2
7     2221  48.846017   2.260547         1
8     2224  48.844664   2.264386         2
9     2218  48.846017   2.264386         1
10    2216  48.847370   2.264386         1
11    2141  48.848723   2.264386         1
12    2223  48.844664   2.268225         1
13    2217  48.846017   2.268225         2
14    2215  48.847370   2.268225         1
15    2140  48.848723   2.268225         1
16    2132  48.851428   2.268225         1
17    2130  48.852781   2.268225         1
18    2108  48.854134   2.268225         2
19    2106  48.855487   2.268225         1
20    2100  48.856840   2.268225         1
21    2206  48.846017   2.272063         1
22    2204  48.847370   2.272063         2
23    2129  48.848723   2.272063         1
24    2095  48.855487   2.272063         1
25    2087  48.858193   2.272063         1
26    2205  48.846017   2.275902         1
27    2088  48.856840   2.275902         1
28    2086  48.858193   2.275902         1
29    1044  48.863604   2.275902         1
..     ...        ...        ...       ...
651   1341  48.846017   2.402582         1
652   1245  48.851428   2.402582         1
653   1243  48.852781   2.402582         1
654    361  48.867663   2.402582         1
655    359  48.869016   2.402582         1
656    273  48.870369   2.402582         1
657    271  48.871722   2.402582         1
658    265  48.873075   2.402582         1
659   1651  48.833841   2.406421         1
660   1645  48.835194   2.406421         1
661   1643  48.836547   2.406421         1
662   1244  48.851428   2.406421         1
663   1242  48.852781   2.406421         1
664   1220  48.854134   2.406421         1
665    390  48.863604   2.406421         1
666    368  48.864957   2.406421         1
667    270  48.871722   2.406421         1
668    240  48.875780   2.406421         1
669    238  48.877133   2.406421         1
670    232  48.878486   2.406421         1
671   1182  48.846017   2.410260         1
672   1180  48.847370   2.410260         1
673   1142  48.848723   2.410260         1
674   1136  48.852781   2.410260         1
675   1134  48.854134   2.410260         1
676    223  48.863604   2.410260         1
677    222  48.864957   2.410260         1
678    224  48.862252   2.414099         1
679   1150  48.843311   2.440970         1
680   1148  48.844664   2.440970         1

[681 rows x 4 columns]

In [22]:
paris_housing_sales_prices_df = paris_housing_sales_prices_df.sort_values(by=['longitude', 'latitude']).reset_index()
paris_housing_sales_prices_df

index   latitude  longitude  price_by_square_meters
0       7696  48.843853   2.255896                 10479.0
1       7570  48.843611   2.256050                  8289.0
2       7422  48.843323   2.256156                  6634.0
3       7490  48.843434   2.256203                  7854.0
4       7021  48.842536   2.256418                 11038.0
5       7070  48.842631   2.256485                 10906.0
6       5835  48.840263   2.256566                 18708.0
7       6035  48.840644   2.256608                  6237.0
8       6138  48.840815   2.256629                  3738.0
9       5988  48.840537   2.256648                  8600.0
10      6274  48.841041   2.256672                  8079.0
11      7060  48.842607   2.256716                 13446.0
12      7203  48.842857   2.256784                  9369.0
13      6087  48.840717   2.256828                  7468.0
14      7046  48.842585   2.256902                  9010.0
15      7375  48.843206   2.256971                  8170.0
16      5745  48.840093   2.257019                  9107.0
17      7072  48.842637   2.257033                 15769.0
18      7173  48.842813   2.257091                 14110.0
19      7215  48.842887   2.257177                  8336.0
20      5432  48.839429   2.257180                  8118.0
21      5105  48.838703   2.257184                  7250.0
22      7559  48.843587   2.257218                  8834.0
23      5278  48.839094   2.257252                  7557.0
24      5920  48.840408   2.257302                  8108.0
25      6002  48.840566   2.257331                  7221.0
26      7637  48.843751   2.257355                  5593.0
27      7803  48.844036   2.257374                  8200.0
28      6077  48.840701   2.257386                  8631.0
29      6926  48.842348   2.257429                  8611.0
...      ...        ...        ...                     ...
35743  13634  48.853744   2.409670                  6781.0
35744   9175  48.846687   2.409686                  6667.0
35745   7567  48.843603   2.409688                  7750.0
35746   8666  48.845765   2.409691                  9737.0
35747   8763  48.845947   2.409732                  7631.0
35748   7793  48.844024   2.409786                  7469.0
35749  14479  48.855212   2.409795                  6102.0
35750   8342  48.845123   2.409867                  6859.0
35751  13232  48.853129   2.409880                  7093.0
35752  14152  48.854648   2.409892                  7148.0
35753  14082  48.854518   2.409990                  7021.0
35754  14032  48.854423   2.410031                  7275.0
35755  13318  48.853260   2.410059                  5519.0
35756   9831  48.847793   2.410098                  6885.0
35757  13222  48.853112   2.410134                  6096.0
35758  13535  48.853596   2.410284                 21647.0
35759  13230  48.853125   2.410319                  6856.0
35760  10078  48.848253   2.410449                  6226.0
35761   9754  48.847670   2.410476                  8206.0
35762   9892  48.847923   2.410489                  6487.0
35763   9121  48.846606   2.410530                  7278.0
35764   9688  48.847546   2.410794                 94495.0
35765   9817  48.847775   2.410819                  7969.0
35766  10497  48.848923   2.410847                  7436.0
35767  10184  48.848423   2.410879                  5051.0
35768  10350  48.848681   2.410886                  6938.0
35769  10510  48.848948   2.411010                  5223.0
35770  10474  48.848882   2.411018                  7355.0
35771   9060  48.846500   2.411386                  6167.0
35772  10506  48.848946   2.412825                  6176.0

[35773 rows x 4 columns]

In [23]:
transactions = []
avgPrices = []
for i, rowCenters in df_centers.iterrows():
    total = 0
    amount = 0
    centerLatitude = rowCenters["latitude"]
    centerLongitude = rowCenters["longitude"]
    minLongitude = geodesic(meters=maxRadius).destination((centerLatitude, centerLongitude), 270).longitude
    maxLongitude = geodesic(meters=maxRadius).destination((centerLatitude, centerLongitude), 90).longitude
    for j, rowPrices in paris_housing_sales_prices_df[(paris_housing_sales_prices_df["longitude"] >= minLongitude) & (paris_housing_sales_prices_df["longitude"] <= maxLongitude)].iterrows():
        if is_in_circle(centerLatitude, centerLongitude, rowPrices["latitude"], rowPrices["longitude"], maxRadius):
            total = total + 1
            amount = amount + rowPrices["price_by_square_meters"]                
            
    transactions.append(total)
    avgPrices.append(0 if total == 0 else round(amount / total, 0))
    print(' {}'.format(total), end='')
print(' done.')    
df_centers["transactions"] = transactions
df_centers["avg_price"] = avgPrices
df_centers.to_csv("df_centers_with_transactions.csv")
df_centers

 5 19 10 0 87 66 63 73 50 44 85 101 24 13 68 107 101 92 90 84 61 38 56 79 90 55 9 101 111 63 67 36 12 7 6 34 40 13 25 59 68 57 54 52 31 80 106 66 49 21 19 0 24 57 71 82 73 72 21 18 13 37 38 26 11 28 64 60 67 79 83 63 109 29 77 68 75 61 42 77 85 37 103 85 92 113 112 122 101 49 21 20 35 26 8 30 123 103 120 128 88 90 68 14 32 20 22 39 87 117 93 74 8 27 52 86 49 63 45 30 5 14 33 37 68 117 7 18 72 101 71 102 21 71 125 69 76 79 51 75 73 81 31 38 55 9 7 36 58 38 16 42 60 74 85 60 96 80 25 36 5 11 6 4 0 0 0 11 46 43 88 24 17 9 169 150 68 66 66 79 102 14 6 40 48 100 102 131 109 32 38 48 66 71 71 30 44 48 26 11 0 1 38 33 38 46 80 94 107 210 265 2 39 81 85 81 15 35 57 61 57 58 93 94 51 39 70 70 67 19 33 22 21 42 77 119 117 133 144 136 173 128 120 97 108 21 37 53 86 90 72 78 94 91 80 96 22 54 55 11 11 17 20 26 120 95 110 75 75 45 16 35 30 108 119 99 77 89 62 20 7 24 33 32 39 134 148 125 37 21 117 150 0 12 13 57 28 15 20 52 91 135 139 131 144 176 234 116 139 18 23 75 118 18 19 58 61 33 42 49 52 66 

index   latitude  longitude  stations  transactions  avg_price
0     2476  48.836547   2.256708         1             5     7171.0
1     2262  48.837899   2.256708         1            19     8119.0
2     2220  48.847370   2.256708         1            10    11333.0
3     2145  48.848723   2.256708         1             0        0.0
4     2251  48.841958   2.260547         1            87     9929.0
5     2229  48.843311   2.260547         1            66     9837.0
6     2227  48.844664   2.260547         2            63    10478.0
7     2221  48.846017   2.260547         1            73    10780.0
8     2224  48.844664   2.264386         2            50     9575.0
9     2218  48.846017   2.264386         1            44    10701.0
10    2216  48.847370   2.264386         1            85    10592.0
11    2141  48.848723   2.264386         1           101    10759.0
12    2223  48.844664   2.268225         1            24     9264.0
13    2217  48.846017   2.268225         2            13    12963.0
14    2215  48.847370   2.268225         1            68    10490.0
15    2140  48.848723   2.268225         1           107     9936.0
16    2132  48.851428   2.268225         1           101    11385.0
17    2130  48.852781   2.268225         1            92    12351.0
18    2108  48.854134   2.268225         2            90    11955.0
19    2106  48.855487   2.268225         1            84    10274.0
20    2100  48.856840   2.268225         1            61    10562.0
21    2206  48.846017   2.272063         1            38     8663.0
22    2204  48.847370   2.272063         2            56     8610.0
23    2129  48.848723   2.272063         1            79     9242.0
24    2095  48.855487   2.272063         1            90    10164.0
25    2087  48.858193   2.272063         1            55    13641.0
26    2205  48.846017   2.275902         1             9     8129.0
27    2088  48.856840   2.275902         1           101    10923.0
28    2086  48.858193   2.275902         1           111    10886.0
29    1044  48.863604   2.275902         1            63    14231.0
..     ...        ...        ...       ...           ...        ...
651   1341  48.846017   2.402582         1            79     8825.0
652   1245  48.851428   2.402582         1            68     8600.0
653   1243  48.852781   2.402582         1            67     7666.0
654    361  48.867663   2.402582         1            78     8358.0
655    359  48.869016   2.402582         1            87     7835.0
656    273  48.870369   2.402582         1            55     9598.0
657    271  48.871722   2.402582         1            46     8555.0
658    265  48.873075   2.402582         1            46     8645.0
659   1651  48.833841   2.406421         1            14    13358.0
660   1645  48.835194   2.406421         1            39    10056.0
661   1643  48.836547   2.406421         1            58     9048.0
662   1244  48.851428   2.406421         1            75     8081.0
663   1242  48.852781   2.406421         1            86     7745.0
664   1220  48.854134   2.406421         1            62    12079.0
665    390  48.863604   2.406421         1            54     7950.0
666    368  48.864957   2.406421         1            51     8921.0
667    270  48.871722   2.406421         1            40     7615.0
668    240  48.875780   2.406421         1            17    15552.0
669    238  48.877133   2.406421         1            21    13541.0
670    232  48.878486   2.406421         1            14    17231.0
671   1182  48.846017   2.410260         1            43     9779.0
672   1180  48.847370   2.410260         1            30    10346.0
673   1142  48.848723   2.410260         1            18    11836.0
674   1136  48.852781   2.410260         1            22     7756.0
675   1134  48.854134   2.410260         1            21     7837.0
676    223  48.863604   2.410260         1             8     6602.0
677    222  48.864957   2.410260         1             8    1

In [36]:
df_centers = pd.read_csv("df_centers_with_transactions.csv")
df_centers = df_centers[["latitude", "longitude", "stations", "transactions", "avg_price"]]
df_centers

latitude  longitude  stations  transactions  avg_price
0    48.836547   2.256708         1             5     7171.0
1    48.837899   2.256708         1            19     8119.0
2    48.847370   2.256708         1            10    11333.0
3    48.848723   2.256708         1             0        0.0
4    48.841958   2.260547         1            87     9929.0
5    48.843311   2.260547         1            66     9837.0
6    48.844664   2.260547         2            63    10478.0
7    48.846017   2.260547         1            73    10780.0
8    48.844664   2.264386         2            50     9575.0
9    48.846017   2.264386         1            44    10701.0
10   48.847370   2.264386         1            85    10592.0
11   48.848723   2.264386         1           101    10759.0
12   48.844664   2.268225         1            24     9264.0
13   48.846017   2.268225         2            13    12963.0
14   48.847370   2.268225         1            68    10490.0
15   48.848723   2.268225         1           107     9936.0
16   48.851428   2.268225         1           101    11385.0
17   48.852781   2.268225         1            92    12351.0
18   48.854134   2.268225         2            90    11955.0
19   48.855487   2.268225         1            84    10274.0
20   48.856840   2.268225         1            61    10562.0
21   48.846017   2.272063         1            38     8663.0
22   48.847370   2.272063         2            56     8610.0
23   48.848723   2.272063         1            79     9242.0
24   48.855487   2.272063         1            90    10164.0
25   48.858193   2.272063         1            55    13641.0
26   48.846017   2.275902         1             9     8129.0
27   48.856840   2.275902         1           101    10923.0
28   48.858193   2.275902         1           111    10886.0
29   48.863604   2.275902         1            63    14231.0
..         ...        ...       ...           ...        ...
651  48.846017   2.402582         1            79     8825.0
652  48.851428   2.402582         1            68     8600.0
653  48.852781   2.402582         1            67     7666.0
654  48.867663   2.402582         1            78     8358.0
655  48.869016   2.402582         1            87     7835.0
656  48.870369   2.402582         1            55     9598.0
657  48.871722   2.402582         1            46     8555.0
658  48.873075   2.402582         1            46     8645.0
659  48.833841   2.406421         1            14    13358.0
660  48.835194   2.406421         1            39    10056.0
661  48.836547   2.406421         1            58     9048.0
662  48.851428   2.406421         1            75     8081.0
663  48.852781   2.406421         1            86     7745.0
664  48.854134   2.406421         1            62    12079.0
665  48.863604   2.406421         1            54     7950.0
666  48.864957   2.406421         1            51     8921.0
667  48.871722   2.406421         1            40     7615.0
668  48.875780   2.406421         1            17    15552.0
669  48.877133   2.406421         1            21    13541.0
670  48.878486   2.406421         1            14    17231.0
671  48.846017   2.410260         1            43     9779.0
672  48.847370   2.410260         1            30    10346.0
673  48.848723   2.410260         1            18    11836.0
674  48.852781   2.410260         1            22     7756.0
675  48.854134   2.410260         1            21     7837.0
676  48.863604   2.410260         1             8     6602.0
677  48.864957   2.410260         1             8    10155.0
678  48.862252   2.414099         1             0        0.0
679  48.843311   2.440970         1             0        0.0
680  48.844664   2.440970         1             0        0.0

[681 rows x 5 columns]

As we now have the total amount of transactions for each potential location, we will keep only those which have at least 10 transactions, which means that we expect more than one transaction every 6 months (2 by year in 5 years). We consider that below this threshold, it would be too hard to find a house or an apartment anyway so no need to keep them. 

Thanks to this new filter, we end up with **613** potential locations. 

In [37]:
df_centers = df_centers[df_centers["transactions"] > 10]
df_centers

latitude  longitude  stations  transactions  avg_price
1    48.837899   2.256708         1            19     8119.0
4    48.841958   2.260547         1            87     9929.0
5    48.843311   2.260547         1            66     9837.0
6    48.844664   2.260547         2            63    10478.0
7    48.846017   2.260547         1            73    10780.0
8    48.844664   2.264386         2            50     9575.0
9    48.846017   2.264386         1            44    10701.0
10   48.847370   2.264386         1            85    10592.0
11   48.848723   2.264386         1           101    10759.0
12   48.844664   2.268225         1            24     9264.0
13   48.846017   2.268225         2            13    12963.0
14   48.847370   2.268225         1            68    10490.0
15   48.848723   2.268225         1           107     9936.0
16   48.851428   2.268225         1           101    11385.0
17   48.852781   2.268225         1            92    12351.0
18   48.854134   2.268225         2            90    11955.0
19   48.855487   2.268225         1            84    10274.0
20   48.856840   2.268225         1            61    10562.0
21   48.846017   2.272063         1            38     8663.0
22   48.847370   2.272063         2            56     8610.0
23   48.848723   2.272063         1            79     9242.0
24   48.855487   2.272063         1            90    10164.0
25   48.858193   2.272063         1            55    13641.0
27   48.856840   2.275902         1           101    10923.0
28   48.858193   2.275902         1           111    10886.0
29   48.863604   2.275902         1            63    14231.0
30   48.864957   2.275902         1            67    13189.0
31   48.870369   2.275902         1            36    13932.0
32   48.871722   2.275902         1            12    16852.0
35   48.836547   2.279741         1            34     8532.0
..         ...        ...       ...           ...        ...
646  48.836547   2.402582         1            81     9663.0
647  48.837899   2.402582         1            98     9128.0
648  48.840605   2.402582         1            72     8665.0
649  48.841958   2.402582         1            43     8690.0
650  48.844664   2.402582         1            64     9002.0
651  48.846017   2.402582         1            79     8825.0
652  48.851428   2.402582         1            68     8600.0
653  48.852781   2.402582         1            67     7666.0
654  48.867663   2.402582         1            78     8358.0
655  48.869016   2.402582         1            87     7835.0
656  48.870369   2.402582         1            55     9598.0
657  48.871722   2.402582         1            46     8555.0
658  48.873075   2.402582         1            46     8645.0
659  48.833841   2.406421         1            14    13358.0
660  48.835194   2.406421         1            39    10056.0
661  48.836547   2.406421         1            58     9048.0
662  48.851428   2.406421         1            75     8081.0
663  48.852781   2.406421         1            86     7745.0
664  48.854134   2.406421         1            62    12079.0
665  48.863604   2.406421         1            54     7950.0
666  48.864957   2.406421         1            51     8921.0
667  48.871722   2.406421         1            40     7615.0
668  48.875780   2.406421         1            17    15552.0
669  48.877133   2.406421         1            21    13541.0
670  48.878486   2.406421         1            14    17231.0
671  48.846017   2.410260         1            43     9779.0
672  48.847370   2.410260         1            30    10346.0
673  48.848723   2.410260         1            18    11836.0
674  48.852781   2.410260         1            22     7756.0
675  48.854134   2.410260         1            21     7837.0

[613 rows x 5 columns]

It is now time to use **Foursquare** to retrieve all the venues close to each remaining potential location.

In [32]:
# The code was removed by Watson Studio for sharing.

In [33]:
VERSION = '20180604'
LIMIT = maxRadius

In [34]:
def get_total_venues(row):
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, row["latitude"], row["longitude"], VERSION, maxRadius, LIMIT)
    results = requests.get(url).json()
    try:
        return len(results['response']['groups'][0]['items'])
    except:
        return 0

In [38]:
df_centers['total_venues'] = df_centers.apply(get_total_venues, axis=1)
df_centers.to_csv("df_centers_with_transactions_and_venues.csv")
df_centers

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if __name__ == '__main__':


latitude  longitude  stations  transactions  avg_price  total_venues
1    48.837899   2.256708         1            19     8119.0            14
4    48.841958   2.260547         1            87     9929.0             3
5    48.843311   2.260547         1            66     9837.0             2
6    48.844664   2.260547         2            63    10478.0             3
7    48.846017   2.260547         1            73    10780.0             6
8    48.844664   2.264386         2            50     9575.0             2
9    48.846017   2.264386         1            44    10701.0             2
10   48.847370   2.264386         1            85    10592.0            10
11   48.848723   2.264386         1           101    10759.0            15
12   48.844664   2.268225         1            24     9264.0             1
13   48.846017   2.268225         2            13    12963.0             6
14   48.847370   2.268225         1            68    10490.0             9
15   48.848723   2.268225         1           107     9936.0            11
16   48.851428   2.268225         1           101    11385.0             8
17   48.852781   2.268225         1            92    12351.0             4
18   48.854134   2.268225         2            90    11955.0            11
19   48.855487   2.268225         1            84    10274.0            11
20   48.856840   2.268225         1            61    10562.0             4
21   48.846017   2.272063         1            38     8663.0             9
22   48.847370   2.272063         2            56     8610.0             9
23   48.848723   2.272063         1            79     9242.0             9
24   48.855487   2.272063         1            90    10164.0             7
25   48.858193   2.272063         1            55    13641.0             9
27   48.856840   2.275902         1           101    10923.0            22
28   48.858193   2.275902         1           111    10886.0            18
29   48.863604   2.275902         1            63    14231.0            14
30   48.864957   2.275902         1            67    13189.0             7
31   48.870369   2.275902         1            36    13932.0             7
32   48.871722   2.275902         1            12    16852.0             5
35   48.836547   2.279741         1            34     8532.0            21
..         ...        ...       ...           ...        ...           ...
646  48.836547   2.402582         1            81     9663.0            14
647  48.837899   2.402582         1            98     9128.0            13
648  48.840605   2.402582         1            72     8665.0             0
649  48.841958   2.402582         1            43     8690.0             4
650  48.844664   2.402582         1            64     9002.0            10
651  48.846017   2.402582         1            79     8825.0            11
652  48.851428   2.402582         1            68     8600.0            10
653  48.852781   2.402582         1            67     7666.0            10
654  48.867663   2.402582         1            78     8358.0            10
655  48.869016   2.402582         1            87     7835.0             9
656  48.870369   2.402582         1            55     9598.0             7
657  48.871722   2.402582         1            46     8555.0             7
658  48.873075   2.402582         1            46     8645.0             7
659  48.833841   2.406421         1            14    13358.0            10
660  48.835194   2.406421         1            39    10056.0            18
661  48.836547   2.406421         1            58     9048.0            16
662  48.851428   2.406421         1            75     8081.0             5
663  48.852781   2.406421         1            86     7745.0            12
664  48.854134   2.406421         1            62    12079.0             8
665  48.863604   2.406421         1            54     7950.0            10
666  48.864957   2.406421         1            51     8921.0             9
667  48.871722   2.406421      

In [39]:
df_centers = pd.read_csv("df_centers_with_transactions_and_venues.csv")
df_centers = df_centers[["latitude", "longitude", "stations", "transactions", "avg_price", "total_venues"]]
df_centers

latitude  longitude  stations  transactions  avg_price  total_venues
0    48.837899   2.256708         1            19     8119.0            14
1    48.841958   2.260547         1            87     9929.0             3
2    48.843311   2.260547         1            66     9837.0             2
3    48.844664   2.260547         2            63    10478.0             3
4    48.846017   2.260547         1            73    10780.0             6
5    48.844664   2.264386         2            50     9575.0             2
6    48.846017   2.264386         1            44    10701.0             2
7    48.847370   2.264386         1            85    10592.0            10
8    48.848723   2.264386         1           101    10759.0            15
9    48.844664   2.268225         1            24     9264.0             1
10   48.846017   2.268225         2            13    12963.0             6
11   48.847370   2.268225         1            68    10490.0             9
12   48.848723   2.268225         1           107     9936.0            11
13   48.851428   2.268225         1           101    11385.0             8
14   48.852781   2.268225         1            92    12351.0             4
15   48.854134   2.268225         2            90    11955.0            11
16   48.855487   2.268225         1            84    10274.0            11
17   48.856840   2.268225         1            61    10562.0             4
18   48.846017   2.272063         1            38     8663.0             9
19   48.847370   2.272063         2            56     8610.0             9
20   48.848723   2.272063         1            79     9242.0             9
21   48.855487   2.272063         1            90    10164.0             7
22   48.858193   2.272063         1            55    13641.0             9
23   48.856840   2.275902         1           101    10923.0            22
24   48.858193   2.275902         1           111    10886.0            18
25   48.863604   2.275902         1            63    14231.0            14
26   48.864957   2.275902         1            67    13189.0             7
27   48.870369   2.275902         1            36    13932.0             7
28   48.871722   2.275902         1            12    16852.0             5
29   48.836547   2.279741         1            34     8532.0            21
..         ...        ...       ...           ...        ...           ...
583  48.836547   2.402582         1            81     9663.0            14
584  48.837899   2.402582         1            98     9128.0            13
585  48.840605   2.402582         1            72     8665.0             0
586  48.841958   2.402582         1            43     8690.0             4
587  48.844664   2.402582         1            64     9002.0            10
588  48.846017   2.402582         1            79     8825.0            11
589  48.851428   2.402582         1            68     8600.0            10
590  48.852781   2.402582         1            67     7666.0            10
591  48.867663   2.402582         1            78     8358.0            10
592  48.869016   2.402582         1            87     7835.0             9
593  48.870369   2.402582         1            55     9598.0             7
594  48.871722   2.402582         1            46     8555.0             7
595  48.873075   2.402582         1            46     8645.0             7
596  48.833841   2.406421         1            14    13358.0            10
597  48.835194   2.406421         1            39    10056.0            18
598  48.836547   2.406421         1            58     9048.0            16
599  48.851428   2.406421         1            75     8081.0             5
600  48.852781   2.406421         1            86     7745.0            12
601  48.854134   2.406421         1            62    12079.0             8
602  48.863604   2.406421         1            54     7950.0            10
603  48.864957   2.406421         1            51     8921.0             9
604  48.871722   2.406421      

As we expect a living place with a lot of activities around it, no need to keep potential locations without any venues, which allows reducing the total amount of potential locations to **611**.

In [40]:
df_centers = df_centers[df_centers["total_venues"] > 0]
df_centers

latitude  longitude  stations  transactions  avg_price  total_venues
0    48.837899   2.256708         1            19     8119.0            14
1    48.841958   2.260547         1            87     9929.0             3
2    48.843311   2.260547         1            66     9837.0             2
3    48.844664   2.260547         2            63    10478.0             3
4    48.846017   2.260547         1            73    10780.0             6
5    48.844664   2.264386         2            50     9575.0             2
6    48.846017   2.264386         1            44    10701.0             2
7    48.847370   2.264386         1            85    10592.0            10
8    48.848723   2.264386         1           101    10759.0            15
9    48.844664   2.268225         1            24     9264.0             1
10   48.846017   2.268225         2            13    12963.0             6
11   48.847370   2.268225         1            68    10490.0             9
12   48.848723   2.268225         1           107     9936.0            11
13   48.851428   2.268225         1           101    11385.0             8
14   48.852781   2.268225         1            92    12351.0             4
15   48.854134   2.268225         2            90    11955.0            11
16   48.855487   2.268225         1            84    10274.0            11
17   48.856840   2.268225         1            61    10562.0             4
18   48.846017   2.272063         1            38     8663.0             9
19   48.847370   2.272063         2            56     8610.0             9
20   48.848723   2.272063         1            79     9242.0             9
21   48.855487   2.272063         1            90    10164.0             7
22   48.858193   2.272063         1            55    13641.0             9
23   48.856840   2.275902         1           101    10923.0            22
24   48.858193   2.275902         1           111    10886.0            18
25   48.863604   2.275902         1            63    14231.0            14
26   48.864957   2.275902         1            67    13189.0             7
27   48.870369   2.275902         1            36    13932.0             7
28   48.871722   2.275902         1            12    16852.0             5
29   48.836547   2.279741         1            34     8532.0            21
..         ...        ...       ...           ...        ...           ...
582  48.879839   2.398743         1            24    14407.0             1
583  48.836547   2.402582         1            81     9663.0            14
584  48.837899   2.402582         1            98     9128.0            13
586  48.841958   2.402582         1            43     8690.0             4
587  48.844664   2.402582         1            64     9002.0            10
588  48.846017   2.402582         1            79     8825.0            11
589  48.851428   2.402582         1            68     8600.0            10
590  48.852781   2.402582         1            67     7666.0            10
591  48.867663   2.402582         1            78     8358.0            10
592  48.869016   2.402582         1            87     7835.0             9
593  48.870369   2.402582         1            55     9598.0             7
594  48.871722   2.402582         1            46     8555.0             7
595  48.873075   2.402582         1            46     8645.0             7
596  48.833841   2.406421         1            14    13358.0            10
597  48.835194   2.406421         1            39    10056.0            18
598  48.836547   2.406421         1            58     9048.0            16
599  48.851428   2.406421         1            75     8081.0             5
600  48.852781   2.406421         1            86     7745.0            12
601  48.854134   2.406421         1            62    12079.0             8
602  48.863604   2.406421         1            54     7950.0            10
603  48.864957   2.406421         1            51     8921.0             9
604  48.871722   2.406421      

At this stage, all the remaining potential locations are real candidates so now it is time to cluster them based on the total amount of transactions, average price and the total amount of venues. 

To cluster our locations, we will use K-Means Clustering's technique to identify all potential locations that are similar.

In [41]:
df_centers_data_only = df_centers[["transactions", "avg_price", "total_venues"]]
df_centers_data_only

transactions  avg_price  total_venues
0              19     8119.0            14
1              87     9929.0             3
2              66     9837.0             2
3              63    10478.0             3
4              73    10780.0             6
5              50     9575.0             2
6              44    10701.0             2
7              85    10592.0            10
8             101    10759.0            15
9              24     9264.0             1
10             13    12963.0             6
11             68    10490.0             9
12            107     9936.0            11
13            101    11385.0             8
14             92    12351.0             4
15             90    11955.0            11
16             84    10274.0            11
17             61    10562.0             4
18             38     8663.0             9
19             56     8610.0             9
20             79     9242.0             9
21             90    10164.0             7
22             55    13641.0             9
23            101    10923.0            22
24            111    10886.0            18
25             63    14231.0            14
26             67    13189.0             7
27             36    13932.0             7
28             12    16852.0             5
29             34     8532.0            21
..            ...        ...           ...
582            24    14407.0             1
583            81     9663.0            14
584            98     9128.0            13
586            43     8690.0             4
587            64     9002.0            10
588            79     8825.0            11
589            68     8600.0            10
590            67     7666.0            10
591            78     8358.0            10
592            87     7835.0             9
593            55     9598.0             7
594            46     8555.0             7
595            46     8645.0             7
596            14    13358.0            10
597            39    10056.0            18
598            58     9048.0            16
599            75     8081.0             5
600            86     7745.0            12
601            62    12079.0             8
602            54     7950.0            10
603            51     8921.0             9
604            40     7615.0             9
605            17    15552.0             8
606            21    13541.0             8
607            14    17231.0             5
608            43     9779.0             4
609            30    10346.0             6
610            18    11836.0             4
611            22     7756.0            10
612            21     7837.0            14

[611 rows x 3 columns]

Now let's normalize the dataset to be able to use the K-Means Clustering's technique

In [42]:
X = df_centers_data_only.values[:,]
X = np.nan_to_num(X)
cluster_dataset = StandardScaler().fit_transform(X)
cluster_dataset

array([[-1.27503427, -1.09566235, -0.39233782],
       [ 0.44187138, -0.38754433, -1.35295803],
       [-0.08834948, -0.42353707, -1.44028714],
       ...,
       [-1.30028288,  0.35852257, -1.26562892],
       [-1.19928843, -1.23767719, -0.74165426],
       [-1.22453704, -1.20598793, -0.39233782]])

We can now launch the K-Means Clustering's technique with an expected amount of cluster set to 5

In [43]:
num_clusters = 5

k_means = KMeans(init="k-means++", n_clusters=num_clusters, n_init=12)
k_means.fit(cluster_dataset)
labels = k_means.labels_

print(labels)

[1 0 1 1 0 1 1 0 0 1 4 0 0 0 0 0 0 1 1 1 0 0 4 0 0 4 4 4 4 1 1 1 1 4 1 1 1
 2 2 0 0 2 4 2 2 1 1 0 0 0 2 1 1 1 1 1 4 4 4 0 4 0 0 0 0 3 1 2 2 2 2 4 2 0
 1 0 0 0 0 0 0 0 1 4 4 4 4 2 0 0 0 0 2 2 2 4 2 2 2 2 2 3 2 2 1 1 0 1 0 1 4
 4 2 2 0 0 1 0 0 0 0 4 4 3 0 0 0 1 0 0 0 4 4 4 2 2 2 1 1 1 0 0 1 0 0 1 4 4
 4 4 4 0 1 1 3 3 2 0 0 0 0 4 4 2 0 0 0 0 1 2 2 2 0 2 4 4 4 4 4 2 2 1 1 0 0
 3 3 3 1 2 0 0 1 1 2 2 4 2 2 2 4 4 4 4 4 2 2 4 1 2 0 3 3 3 3 0 0 0 0 2 3 1
 4 2 2 2 4 4 2 2 4 4 4 2 2 2 2 2 2 2 0 2 0 1 1 1 1 2 1 3 3 4 2 2 2 2 2 2 1
 1 3 3 3 1 1 3 3 4 4 2 2 1 2 1 0 3 3 3 3 3 3 0 0 1 1 2 3 4 4 4 2 2 2 2 2 2
 2 2 3 3 1 1 2 3 3 4 4 2 4 3 2 3 2 3 3 0 2 3 3 0 1 1 1 1 2 2 3 3 3 4 2 3 3
 3 3 3 3 3 3 2 2 3 3 0 0 0 3 3 0 0 0 0 0 0 0 0 0 0 0 3 2 0 2 2 3 2 3 3 0 0
 3 3 3 0 1 1 0 0 2 2 2 1 0 1 1 3 2 3 0 3 3 3 0 0 0 0 2 1 0 4 1 1 1 1 1 4 4
 2 3 3 3 0 0 3 1 1 0 0 0 0 0 1 1 3 2 2 0 0 1 0 1 1 1 1 4 1 1 0 2 2 2 2 2 2
 0 3 3 1 1 1 1 1 4 2 2 2 2 1 1 1 0 3 0 1 1 1 0 2 1 1 1 1 2 2 3 0 2 0 0 2 3
 1 1 1 1 1 1 1 1 3 3 0 0 

Add the resulting labels to the DataFrame

In [44]:
df_centers["label"] = labels
df_centers_data_only["label"] = labels
df_centers

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if __name__ == '__main__':
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app


latitude  longitude  stations  transactions  avg_price  total_venues  \
0    48.837899   2.256708         1            19     8119.0            14   
1    48.841958   2.260547         1            87     9929.0             3   
2    48.843311   2.260547         1            66     9837.0             2   
3    48.844664   2.260547         2            63    10478.0             3   
4    48.846017   2.260547         1            73    10780.0             6   
5    48.844664   2.264386         2            50     9575.0             2   
6    48.846017   2.264386         1            44    10701.0             2   
7    48.847370   2.264386         1            85    10592.0            10   
8    48.848723   2.264386         1           101    10759.0            15   
9    48.844664   2.268225         1            24     9264.0             1   
10   48.846017   2.268225         2            13    12963.0             6   
11   48.847370   2.268225         1            68    10490.0             9   
12   48.848723   2.268225         1           107     9936.0            11   
13   48.851428   2.268225         1           101    11385.0             8   
14   48.852781   2.268225         1            92    12351.0             4   
15   48.854134   2.268225         2            90    11955.0            11   
16   48.855487   2.268225         1            84    10274.0            11   
17   48.856840   2.268225         1            61    10562.0             4   
18   48.846017   2.272063         1            38     8663.0             9   
19   48.847370   2.272063         2            56     8610.0             9   
20   48.848723   2.272063         1            79     9242.0             9   
21   48.855487   2.272063         1            90    10164.0             7   
22   48.858193   2.272063         1            55    13641.0             9   
23   48.856840   2.275902         1           101    10923.0            22   
24   48.858193   2.275902         1           111    10886.0            18   
25   48.863604   2.275902         1            63    14231.0            14   
26   48.864957   2.275902         1            67    13189.0             7   
27   48.870369   2.275902         1            36    13932.0             7   
28   48.871722   2.275902         1            12    16852.0             5   
29   48.836547   2.279741         1            34     8532.0            21   
..         ...        ...       ...           ...        ...           ...   
582  48.879839   2.398743         1            24    14407.0             1   
583  48.836547   2.402582         1            81     9663.0            14   
584  48.837899   2.402582         1            98     9128.0            13   
586  48.841958   2.402582         1            43     8690.0             4   
587  48.844664   2.402582         1            64     9002.0            10   
588  48.846017   2.402582         1            79     8825.0            11   
589  48.851428   2.402582         1            68     8600.0            10   
590  48.852781   2.402582         1            67     7666.0            10   
591  48.867663   2.402582         1            78     8358.0            10   
592  48.869016   2.402582         1            87     7835.0             9   
593  48.870369   2.402582         1            55     9598.0             7   
594  48.871722   2.402582         1            46     8555.0             7   
595  48.873075   2.402582         1            46     8645.0             7   
596  48.833841   2.406421         1            14    13358.0            10   
597  48.835194   2.406421         1            39    10056.0            18   
598  48.836547   2.406421         1            58     9048.0            16   
599  48.851428   2.406421         1            75     8081.0             5   
600  48.852781   2.406421         1            86     7745.0            12   
601  48.854134   2.406421         1            62    12079.0             8   
602  48.863604   2.406421   

In [45]:
colors = [
    'orange',
    'lightgreen',
    'lightblue',
    'purple',
    'beige',
]

Display all the potential locations with a specific color for each cluster

In [46]:
map_paris = folium.Map(location=paris_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_paris) #cartodbpositron cartodbdark_matter
folium.GeoJson(paris_boroughs, style_function=boroughs_style, name='geojson').add_to(map_paris)
for center in df_centers.values.tolist():
    folium.CircleMarker(center[0:2], radius=3, color=colors[int(center[-1])], fill=True, fill_color=colors[int(center[-1])], fill_opacity=1).add_to(map_paris)
map_paris

Let's compute the average value for each group to find what could be the best choice

In [47]:
df_centers_data_only = df_centers_data_only.groupby('label').mean()
df_centers_data_only

transactions     avg_price  total_venues
label                                          
0         92.690476   9981.857143     14.857143
1         40.127778   9263.650000      9.488889
2         58.552632  11586.640351     30.596491
3        133.987013  11329.831169     32.948052
4         37.180556  15752.597222     14.861111

According to the result above, the best possible value for money (it may depend on the stakeholder) seems to be the cluster #3 as it is where we have the biggest amount of transactions which means that it should be easy to buy or sell a house or an apartment there, and the biggest amount of venues nearby indicating that we have a lot of activities nearby, and all this for a middle average price.

In [48]:
chosenCluster = 3

Let's display only the potential locations of the chosen cluster

In [49]:
map_paris = folium.Map(location=paris_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_paris) #cartodbpositron cartodbdark_matter
folium.GeoJson(paris_boroughs, style_function=boroughs_style, name='geojson').add_to(map_paris)
for center in df_centers[df_centers["label"] == chosenCluster].values.tolist():
    folium.CircleMarker(center[0:2], radius=3, color=colors[int(center[-1])], fill=True, fill_color=colors[int(center[-1])], fill_opacity=1).add_to(map_paris)
map_paris

We will keep only the potential locations of the chosen cluster which allows reducing the total amount of potential locations to **75**.

In [50]:
df_centers_target = df_centers[df_centers["label"] == chosenCluster]
df_centers_target

latitude  longitude  stations  transactions  avg_price  total_venues  \
65   48.850075   2.291257         1           109    10665.0            30   
101  48.879839   2.298935         1           117    11736.0            24   
123  48.855487   2.306612         1           125    13331.0            48   
154  48.832488   2.318129         1           169     9978.0            25   
155  48.833841   2.318129         1           150    10980.0            26   
185  48.882545   2.321968         1           107     9700.0            35   
186  48.889309   2.321968         1           210     9744.0            20   
187  48.890662   2.321968         1           265     9494.0            14   
211  48.881192   2.325806         1           119     9593.0            27   
212  48.882545   2.325806         1           117     9983.0            32   
213  48.883898   2.325806         1           133    10425.0            41   
214  48.886604   2.325806         1           144    11428.0            21   
220  48.833841   2.329645         2           108    11118.0            29   
249  48.851428   2.333484         2           108    15274.0            38   
250  48.852781   2.333484         2           119    15381.0            58   
260  48.882545   2.333484         1           134    10092.0            35   
261  48.883898   2.333484         1           148    11224.0            28   
262  48.885251   2.333484         1           125    10970.0            30   
265  48.851428   2.337323         1           117    16170.0            42   
266  48.852781   2.337323         2           150    16327.0            67   
275  48.878486   2.337323         1           135    10560.0            28   
276  48.879839   2.337323         1           139    10526.0            38   
277  48.881192   2.337323         1           131    11045.0            38   
278  48.882545   2.337323         1           144    10718.0            25   
279  48.883898   2.337323         1           176    11181.0            33   
280  48.885251   2.337323         1           234    11932.0            36   
286  48.852781   2.341162         1           118    14140.0            34   
298  48.889309   2.341162         1           136    10910.0            21   
299  48.890662   2.341162         1           169     9873.0            15   
303  48.851428   2.345000         1           121    11992.0            59   
..         ...        ...       ...           ...        ...           ...   
338  48.870369   2.348839         1           125     9564.0            30   
341  48.877133   2.348839         1           118    10233.0            34   
342  48.878486   2.348839         1           141     9932.0            20   
346  48.886604   2.348839         1           156     8537.0            21   
347  48.887957   2.348839         1           166     8668.0            25   
359  48.844664   2.352678         2           133    12410.0            20   
364  48.859546   2.352678         1            97    11517.0            42   
366  48.862252   2.352678         1           109    11281.0            38   
367  48.864957   2.352678         1           134    11273.0            33   
370  48.869016   2.352678         1           152    11303.0            21   
371  48.870369   2.352678         1           133    11973.0            23   
372  48.878486   2.352678         1            99    10626.0            30   
385  48.852781   2.356517         1           103    15964.0            29   
387  48.864957   2.356517         1           146    10727.0            34   
389  48.869016   2.356517         1           129    12243.0            34   
390  48.870369   2.356517         1           118    12850.0            33   
391  48.871722   2.356517         1           121    11496.0            32   
408  48.855487   2.360355         1           111    11737.0            54   
409  48.866310   2.360355         1           124    12556.0            26   
410  48.867663   2.360355   

In [55]:
def get_address(row):
    url = 'https://nominatim.openstreetmap.org/reverse?format=jsonv2&lat={}&lon={}'.format(row["latitude"], row["longitude"])
    result = requests.get(url).json()
    return result["display_name"]

As the final step, let's retrieve the address of what we consider as the best locations.

In [56]:
df_centers_target['address'] = df_centers.apply(get_address, axis=1)
df_centers_target.to_csv("df_centers_target.csv")
df_centers_target

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if __name__ == '__main__':


latitude  longitude  stations  transactions  avg_price  total_venues  \
65   48.850075   2.291257         1           109    10665.0            30   
101  48.879839   2.298935         1           117    11736.0            24   
123  48.855487   2.306612         1           125    13331.0            48   
154  48.832488   2.318129         1           169     9978.0            25   
155  48.833841   2.318129         1           150    10980.0            26   
185  48.882545   2.321968         1           107     9700.0            35   
186  48.889309   2.321968         1           210     9744.0            20   
187  48.890662   2.321968         1           265     9494.0            14   
211  48.881192   2.325806         1           119     9593.0            27   
212  48.882545   2.325806         1           117     9983.0            32   
213  48.883898   2.325806         1           133    10425.0            41   
214  48.886604   2.325806         1           144    11428.0            21   
220  48.833841   2.329645         2           108    11118.0            29   
249  48.851428   2.333484         2           108    15274.0            38   
250  48.852781   2.333484         2           119    15381.0            58   
260  48.882545   2.333484         1           134    10092.0            35   
261  48.883898   2.333484         1           148    11224.0            28   
262  48.885251   2.333484         1           125    10970.0            30   
265  48.851428   2.337323         1           117    16170.0            42   
266  48.852781   2.337323         2           150    16327.0            67   
275  48.878486   2.337323         1           135    10560.0            28   
276  48.879839   2.337323         1           139    10526.0            38   
277  48.881192   2.337323         1           131    11045.0            38   
278  48.882545   2.337323         1           144    10718.0            25   
279  48.883898   2.337323         1           176    11181.0            33   
280  48.885251   2.337323         1           234    11932.0            36   
286  48.852781   2.341162         1           118    14140.0            34   
298  48.889309   2.341162         1           136    10910.0            21   
299  48.890662   2.341162         1           169     9873.0            15   
303  48.851428   2.345000         1           121    11992.0            59   
..         ...        ...       ...           ...        ...           ...   
338  48.870369   2.348839         1           125     9564.0            30   
341  48.877133   2.348839         1           118    10233.0            34   
342  48.878486   2.348839         1           141     9932.0            20   
346  48.886604   2.348839         1           156     8537.0            21   
347  48.887957   2.348839         1           166     8668.0            25   
359  48.844664   2.352678         2           133    12410.0            20   
364  48.859546   2.352678         1            97    11517.0            42   
366  48.862252   2.352678         1           109    11281.0            38   
367  48.864957   2.352678         1           134    11273.0            33   
370  48.869016   2.352678         1           152    11303.0            21   
371  48.870369   2.352678         1           133    11973.0            23   
372  48.878486   2.352678         1            99    10626.0            30   
385  48.852781   2.356517         1           103    15964.0            29   
387  48.864957   2.356517         1           146    10727.0            34   
389  48.869016   2.356517         1           129    12243.0            34   
390  48.870369   2.356517         1           118    12850.0            33   
391  48.871722   2.356517         1           121    11496.0            32   
408  48.855487   2.360355         1           111    11737.0            54   
409  48.866310   2.360355         1           124    12556.0            26   
410  48.867663   2.360355   

To get rid of extra information in the address we apply a function to clean up the address

In [57]:
def cleanAddress(address):
    try:
        index = address.index(", Paris")
        return address[0:index]
    except:
        return address    

In [58]:
df_centers_target = pd.read_csv("df_centers_target.csv")
df_centers_target = df_centers_target[["latitude", "longitude", "stations", "transactions", "avg_price", "total_venues", "address"]]
df_centers_target["address"] = df_centers_target["address"].apply(cleanAddress)
df_centers_target

latitude  longitude  stations  transactions  avg_price  total_venues  \
0   48.850075   2.291257         1           109    10665.0            30   
1   48.879839   2.298935         1           117    11736.0            24   
2   48.855487   2.306612         1           125    13331.0            48   
3   48.832488   2.318129         1           169     9978.0            25   
4   48.833841   2.318129         1           150    10980.0            26   
5   48.882545   2.321968         1           107     9700.0            35   
6   48.889309   2.321968         1           210     9744.0            20   
7   48.890662   2.321968         1           265     9494.0            14   
8   48.881192   2.325806         1           119     9593.0            27   
9   48.882545   2.325806         1           117     9983.0            32   
10  48.883898   2.325806         1           133    10425.0            41   
11  48.886604   2.325806         1           144    11428.0            21   
12  48.833841   2.329645         2           108    11118.0            29   
13  48.851428   2.333484         2           108    15274.0            38   
14  48.852781   2.333484         2           119    15381.0            58   
15  48.882545   2.333484         1           134    10092.0            35   
16  48.883898   2.333484         1           148    11224.0            28   
17  48.885251   2.333484         1           125    10970.0            30   
18  48.851428   2.337323         1           117    16170.0            42   
19  48.852781   2.337323         2           150    16327.0            67   
20  48.878486   2.337323         1           135    10560.0            28   
21  48.879839   2.337323         1           139    10526.0            38   
22  48.881192   2.337323         1           131    11045.0            38   
23  48.882545   2.337323         1           144    10718.0            25   
24  48.883898   2.337323         1           176    11181.0            33   
25  48.885251   2.337323         1           234    11932.0            36   
26  48.852781   2.341162         1           118    14140.0            34   
27  48.889309   2.341162         1           136    10910.0            21   
28  48.890662   2.341162         1           169     9873.0            15   
29  48.851428   2.345000         1           121    11992.0            59   
..        ...        ...       ...           ...        ...           ...   
47  48.870369   2.348839         1           125     9564.0            30   
48  48.877133   2.348839         1           118    10233.0            34   
49  48.878486   2.348839         1           141     9932.0            20   
50  48.886604   2.348839         1           156     8537.0            21   
51  48.887957   2.348839         1           166     8668.0            25   
52  48.844664   2.352678         2           133    12410.0            20   
53  48.859546   2.352678         1            97    11517.0            42   
54  48.862252   2.352678         1           109    11281.0            38   
55  48.864957   2.352678         1           134    11273.0            33   
56  48.869016   2.352678         1           152    11303.0            21   
57  48.870369   2.352678         1           133    11973.0            23   
58  48.878486   2.352678         1            99    10626.0            30   
59  48.852781   2.356517         1           103    15964.0            29   
60  48.864957   2.356517         1           146    10727.0            34   
61  48.869016   2.356517         1           129    12243.0            34   
62  48.870369   2.356517         1           118    12850.0            33   
63  48.871722   2.356517         1           121    11496.0            32   
64  48.855487   2.360355         1           111    11737.0            54   
65  48.866310   2.360355         1           124    12556.0            26   
66  48.867663   2.360355         1           109    10333.0            27   
6

Let's now, keep the 10 best locations with the lowest price and highest amount of venues.

In [59]:
df_centers_target_top = df_centers_target.sort_values(['avg_price','total_venues'],ascending=[True, False]).head(10)
df_centers_target_top

latitude  longitude  stations  transactions  avg_price  total_venues  \
50  48.886604   2.348839         1           156     8537.0            21   
51  48.887957   2.348839         1           166     8668.0            25   
35  48.892015   2.345000         1           180     9082.0            29   
71  48.869016   2.371872         1           108     9136.0            28   
73  48.866310   2.375711         1           100     9220.0            49   
36  48.893368   2.345000         2           168     9380.0            28   
7   48.890662   2.321968         1           265     9494.0            14   
76  48.854134   2.383388         1           114     9511.0            31   
47  48.870369   2.348839         1           125     9564.0            30   
8   48.881192   2.325806         1           119     9593.0            27   

                                              address  
50                    86, Rue Myrha, Goutte-d'Or, 18e  
51   8, Rue Custine, Château Rouge, Clignancourt, 18e  
35  Groupe Scolaire Ferdinand Faucon, Rue Ferdinan...  
71  La Maison du Haut-Parleur, 138, Avenue Parment...  
73        9, Cour des Fabriques, Folie-Méricourt, 11e  
36  Église Notre-Dame de Clignancourt, Rue du Mont...  
7                16, Rue des Apennins, Épinettes, 17e  
76  Palais de la Femme, Rue de Charonne, Roquette,...  
47  31, Boulevard de Bonne Nouvelle, Bonne-Nouvell...  
8   Collège Condorcet, Rue de Bucarest, Quartier S...

We can now display the best locations on the map of Paris

In [65]:
map_paris = folium.Map(location=paris_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_paris) #cartodbpositron cartodbdark_matter
folium.GeoJson(paris_boroughs, style_function=boroughs_style, name='geojson').add_to(map_paris)
for i, row in df_centers_target_top.iterrows():
    folium.CircleMarker([row["latitude"], row["longitude"]], popup="<b>Price:</b><br><i>{}€/sm</i><br><b>Total Venues:</b><br><i>{}</i><br><b>Address:</b><br><i>{}</i>".format(row["avg_price"], row["total_venues"], row["address"]).replace("'", "&#39;"), radius=3, color=colors[int(center[-1])], fill=True, fill_color=colors[int(center[-1])], fill_opacity=1).add_to(map_paris)
map_paris

## Results and Discussion 

In our final result, over our 10 proposals, we have 4 locations in the 18th boroughs and 3 locations in the 11th boroughs, which means that we have 70% of our proposals that are in two boroughs, which is actually not really surprising since they are both well-known boroughs for all the activities that you can find there for a relatively cheap price.

Even if those locations are indeed nice place to live, there is still something that has not been considered in this project which is the crime rate due to lack of data. Indeed the northeast part of Paris has the highest crime rate ([more details about the crime rate in this report](https://www.lagazettedescommunes.com/telechargements/2019/06/etude-de-londrp-la-criminalit-sur-les-teritoires-du-grand-paris.pdf)) which is probably the reason why finally end up with those locations, if the crime rate could have been taken into account we would probably have had a different result.

Another thing to consider is the different choices that I made throughout this project that could be considered more or less objectives, those choices allowed to get those particular locations but a stakeholder could have made different choices so we would have ended up with totally different results.

## Conclusion

The purpose of this project was to find the best places to live in Paris close to at least one subway station and close to as many activities as possible for a minimum price. Thanks to the different choices we made, we ended up with 10 best places to live but we realized that the places we found where not necessarily safe places. Due to a lack of data, we could not add the total amount of crimes as a feature to consider when clustering our potential locations, we would have chosen the cluster with the biggest possible amount of transactions and venues and with the lowest possible price and amount of crimes, the result would then have been very different.

To conclude, I would say that it is important to always have all the required data and a clear idea of what the skateholder wants to make sure that we get the best possible results.